This notebook follows the R session where I got the duration and distance matrices. Here, I would like to visualise the advantage of the process with nice graphs and/or maps.

## df_sample for general explanation

In [63]:
import pandas as pd
import geopandas as gpd
from shapely.geometry import shape
from matplotlib.colors import LinearSegmentedColormap
import numpy as np

In [270]:
df_sample=pd.read_csv('data/sample.csv').drop(columns=['coord.x','coord.y'])

In [40]:
gdf=gpd.GeoDataFrame(df_sample, geometry=gpd.points_from_xy(df_sample.x,df_sample.y),crs=4326)

In [48]:
gdf.explore(tiles='carto-db dark_matter')

### Call API from localhost
Storing form: a data frame where each row has an origin and a destination point and the third value is the linestring between the two munis.

In [248]:
import requests
from shapely import LineString, Point
import json

In [208]:
data = []
url_base1 = 'http://localhost:8080/route/v1/driving/'
#api_coords=None
api_coords='19.52660,48.18043;20.95731,48.02448'
url_base2='?overview=full&geometries=geojson&steps=true'

In [210]:
for i in range(0,15):
    for j in range(i,15):
        if i!=j:
            api_coords=(str(df_sample.loc[i, 'x'])+','+str(df_sample.loc[i, 'y'])+';'+
            str(df_sample.loc[j, 'x'])+','+str(df_sample.loc[j, 'y']))
            try:
                response=requests.get(url_base1+api_coords+url_base2)
                route=response.json()['routes'][0]['geometry']['coordinates']
                data.append([df_sample.loc[i,'name'],df_sample.loc[j,'name'],LineString(route)])
            except:
                data.append([df_sample.loc[i,'name'],df_sample.loc[j,'name'],None])

In [226]:
gdf_sample=gpd.GeoDataFrame(pd.DataFrame(data, columns=['from','to','route']),geometry='route',crs=4326)

### Visualise result

In [242]:
import folium

In [274]:
df_sample['geometry']=gpd.points_from_xy(df_sample.x, df_sample.y)

In [276]:
df_sample=gpd.GeoDataFrame(df_sample,crs=4326)

In [280]:
m=gdf_sample.explore(tiles='carto_db positron', name='routes')
m=df_sample.explore(m=m, color='red',name='munis')
folium.LayerControl().add_to(m)
m

## Balaton for a real life example